In [1]:
%reload_ext autoreload
%autoreload 2
import warnings
warnings.filterwarnings("ignore",category =RuntimeWarning)
import numpy as np
import de2 as de
import multiprocessing as mp
import makeqx as mkq
import oldqx as oqx


def rndtop5(x):
    return np.round(x*2.0)/2

def tmm_wrapper2(arg):
    args, kwargs = arg
    return oqx.tmm_eval_wsweep(*args, **kwargs)

def arc_par(pop, **kwargs):
    jobs = []
    pool=mp.Pool(90)
    for indiv in pop:
        #indiv = indiv.reshape((int(indiv.size/2), 2))
        #indiv[:,1] = mkq.digitize_qx(indiv[:,1], dlevels=2)
        indiv = rndtop5(indiv)
        #indiv = indiv.flatten()
        jobs.append((indiv, 0))
    arg = [(j, kwargs) for j in jobs]
    answ = np.array(pool.map(tmm_wrapper2, arg))
    pool.close()
    return answ




In [ ]:
dataset_size = 100000

# parameters of the dataset
num_layers = 16
num_lpoints = 256
lam_min = 300
lam_max = 1200
d_min = 0
d_max = 200

dataset_X = np.random.uniform(0,1,num_layers*dataset_size).astype(float).reshape(dataset_size, num_layers)
lams = np.linspace(lam_min, lam_max, num_lpoints, endpoint=True)
dataset_Y = np.zeros((dataset_size,num_lpoints))

dataset_Y = arc_par(dataset_X,  lam_low=lam_min, lam_high=lam_max, lam_pts = num_lpoints)

(10, 256)

In [ ]:
import h5py
h5f = h5py.File('./datasets/s16_siti.h5', 'w')
h5f.create_dataset('sizes', data=dataset_X)
h5f.create_dataset('spectrum', data=dataset_Y)
h5f.close()